### Constrained Search Problems -- Logic Puzzle 2
3 houses, with nationalities, house-colors and drinks 
from http://www.mensus.net/brain/logic.shtml, puzzle id: 383A.139AE6A2

1. The Swede drinks milk.
2. The person drinking beer lives in the green house.
3. The red house is directly next to the magenta house.
4. The Irish lives directly to the right of the milk drinking person.
5. The first house is magenta.
6. The Spanish drinks espresso.

In [1]:
class MyStack:
    def __init__(self):
        self.array = []
        self.filled = 0
    
    def push(self,item):
        if self.filled == len(self.array):
            self.array.append(item)
        else:
            self.array[self.filled] = item
        self.filled += 1
    
    def pop(self):
        if self.filled > 0:
            self.filled -= 1
            return self.array[self.filled]
        else:
            return None
    
    def isempty(self):
        return self.filled == 0


In [2]:

# Violation checks
def vc_all_different(state):
    '''Rule 1: all assigned property values must be different'''
    allprops = {}
    for prop in Csp.PropertyList:
        allprops[prop] = []
        
    for i in range(state.size()):
        ct = state.get(i)
        #print('vc_all, container: ',i)
        #ct.print()
        for prop in Csp.PropertyList:
            prop_value = ct.getprop(prop)
            if prop_value and prop_value in allprops[prop]:
                #state.print('vc_all_diff failed')
                return False
            allprops[prop].append(ct.getprop(prop))
    
    return True

# -----------------------------------------------------------
''' Property-pair constraints in the same container:'''

def vc_property_pair_in_same_container(state):
    SameContainerPairs = state.csp_parent.ConstraintPairs
    for ct in state.containers:
        for pair in SameContainerPairs:
            prop1,value1,prop2,value2 = pair
            if ct.getprop(prop1) and ct.getprop(prop2):
                if ct.getprop(prop1) == value1 and ct.getprop(prop2) != value2:
                    #state.print('vc_pair failed: should be: %s=%s and %s=%s' % (prop1,value1,prop2,value2))
                    #print('vc_pair failed: should be: %s=%s and %s=%s' % (prop1,value1,prop2,value2))
                    return False
                if ct.getprop(prop1) != value1 and ct.getprop(prop2) == value2:
                    #state.print('vc_pair failed: should be: %s=%s and %s=%s' % (prop1,value1,prop2,value2))
                    #print('vc_pair failed: should be: %s=%s and %s=%s' % (prop1,value1,prop2,value2))
                    return False
    return True

# -----------------------------------------------------------
''' Absolute house constraint:'''

def vc_absolute_position(state):
    AbsolutePositions = state.csp_parent.ConstraintPositions
    for abs_pos in AbsolutePositions:
        pos,prop,value = abs_pos
        ct = state.get(pos)
        if ct.getprop(prop) and ct.getprop(prop) != value:
            #print('vc_absolute failed, should be: %d. %s=%s' % (pos,prop,value))
            return False
    return True

# ---------------------------------------------------------------
'''Neighoring house constraint:'''

def vc_neighbors(state):
    NeighboringProperties = state.csp_parent.ConstraintNeighbors
    for neighbors in NeighboringProperties:
        prop1,value1,prop2,value2,in_order = neighbors
        where1 = find_prop_value(state,prop1,value1)
        where2 = find_prop_value(state,prop2,value2)
        if in_order:
            if where1 >= 0 and where2 >= 0:
                if where2 != where1+1:
                    #state.print('vc_neighbor failed: %s=%s followed by: %s=%s' % (prop1,value1,prop2,value2))
                    #print('vc_neighbor failed: %s=%s followed by %s=%s' % (prop1,value1,prop2,value2))
                    return False
            else:
                if where1 == state.size()-1 or where2 == 0:
                    #state.print('vc_neighbor failed: %s=%s followed by: %s=%s' % (prop1,value1,prop2,value2))
                    #print('vc_neighbor failed: %s=%s followed by %s=%s' % (prop1,value1,prop2,value2))
                    return False
        else:
            if where1 >= 0 and where2 >= 0:
                if where2 != where1+1 and where1 != where2+1:
                    #state.print('vc_neighbor failed: %s=%s near: %s=%s' % (prop1,value1,prop2,value2))
                    #print('vc_neighbor failed: %s=%s near %s=%s' % (prop1,value1,prop2,value2))
                    return False
    return True

# ------------------------------------------------------------------

def find_prop_value(state,prop,value):
    for i in range(state.size()):
        if state.get(i).getprop(prop) == value:
            return i
    return -1


In [3]:
# Inference rules

def inf_all_different(state):
    '''Rule 1: for each property, each of its values must be taken in some container.  
    If exactly one value is not used, fill it in the container that is missing it'''
    vals_taken = {}  # all of the values that are set in all containers, key by property, item is list of used values
    val_is_missing_in = {} # in which container is this property net set, key by property, item is container
    for prop in Csp.PropertyList:
        vals_taken[prop] = []
        val_is_missing_in[prop] = None
        
    # for each property, gather the values used, and store one of the containers that's missing it
    for icontainer in range(state.size()):
        ct = state.get(icontainer)
        for prop in state.csp_parent.PropertyList:
            if ct.getprop(prop):
                vals_taken[prop].append(ct.getprop(prop))
            else:
                val_is_missing_in[prop] = ct
    
    inferred = False
    for prop in state.csp_parent.PropertyList:
        all_vals = state.csp_parent.PropertiesValues[prop]
        # we have a winner?
        if len(vals_taken[prop]) == len(all_vals)-1:
            # find the missing value
            missing_val = None
            for val in all_vals:
                if not val in vals_taken[prop]:
                    missing_val = val
                    break
            ct = val_is_missing_in[prop]
            #print('vals_taken: ',vals_taken[prop],'all_vals: ',all_vals)
            #state.print('inferred (before all diff), missing val is '+missing_val)
            ct.setprop(prop,missing_val)
            inferred = True
            #state.print('inferred: (after all_diff)')
    
    return inferred
            
# ---------------------------------------------------------------------
def inf_property_value_pairs(state):
    pairs = state.csp_parent.ConstraintPairs
    inferred = False
    for i in range(state.size()):
        ct = state.get(i)
        for prop1,val1,prop2,val2 in pairs:
            if ct.getprop(prop1) == val1 and not ct.getprop(prop2):
                # we have a winner
                ct.setprop(prop2,val2)
                inferred = True
                #state.print('inferred: pairs1')
                continue
            if ct.getprop(prop2) == val2 and not ct.getprop(prop1):
                ct.setprop(prop1,val1)
                inferred = True
                #state.print('inferred: pairs2')
    return inferred

# ----------------------------------------------------------
def inf_absolute_position(state):
    triplets = state.csp_parent.ConstraintPositions
    inferred = False
    for pos,prop,value in triplets:
        ct = state.get(pos)
        if not ct.getprop(prop):
            ct.setprop(prop, value)
            inferred = True
            #state.print('inferred: positions')
    return inferred

# ----------------------------------------------------------
def inf_neighbors(state):
    inferred = False
    for neighbors in state.csp_parent.ConstraintNeighbors:
        prop1,value1,prop2,value2,in_order = neighbors
        where1 = find_prop_value(state,prop1,value1)
        where2 = find_prop_value(state,prop2,value2)
        if where1 < 0 and where2 < 0:
            continue
        if where1 >= 0 and where2 >= 0:
            continue
        if in_order:
            if where1 >= 0 and where1 < state.size()-1 and not state.get(where1+1).getprop(prop2):
                #state.print('inferred: neighbors (before): %s, where1=%d where2=%d' % (str(neighbors),where1,where2))
                state.get(where1+1).setprop(prop2,value2)
                #state.print('inferred: neighbors (after): %s, where1=%d where2=%d' % (str(neighbors),where1,where2))
                inferred = True
                continue
            if where2 > 0 and not state.get(where2-1).getprop(prop1):
                #state.print('inferred: neighbors (before): %s, where1=%d where2=%d' % (str(neighbors),where1,where2))
                state.get(where2-1).setprop(prop1,value1)
                #state.print('inferred: neighbors (after): %s, where1=%d where2=%d' % (str(neighbors),where1,where2))
                inferred = True
                continue
        else:
            if where1 == 0 or where1 == state.size()-1 or where2 == 0 or where2 == state.size()-1:
                didit = False
                if where1 == 0 and not state.get(where1+1).getprop(prop2):
                    didit = True
                    state.get(where1+1).setprop(prop2,value2)
                if where1 == state.size()-1 and not state.get(where1-1).getprop(prop2):
                    didit = True
                    state.get(where1-1).setprop(prop2,value2)
                if where2 == 0 and not state.get(where2+1).getprop(prop1):
                    sisit = True
                    state.get(where2+1).setprop(prop1,value1)
                if where2 == state.size()-1 and not state.get(where2-1).getprop(prop1):
                    didit = True
                    state.get(where2-1).setprop(prop1,value1)
                if didit:
                    #state.print('inferred: neighbors: %s' % str(neighbors))
                    inferred = True
                    continue
    return inferred
    

In [4]:

class CSP_Container:

    def __init__(self,csp_parent):
        self.csp_parent = csp_parent
        self.properties = {}
        self.property_list = csp_parent.PropertyList
        for prop in self.property_list:
            self.setprop(prop,None)
    
    def setprop(self,prop,value):
        self.properties[prop] = value
        
    def getprop(self,prop):
        return self.properties[prop]
    
    def clone(self):
        property_list = list(self.properties)
        the_clone = CSP_Container(self.csp_parent)
        for prop in self.property_list:
            the_clone.setprop(prop,self.getprop(prop))
        return the_clone
    
    def print(self,msg=''):
        props=[]
        for prop in self.property_list:
            props.append('%s: %s' % (prop,self.properties[prop]))
        print('%s -- %s' % (msg,', '.join(props)))

class CSP_State:
    
    def __init__(self,csp_parent,ncontainers=None,copy_state=None):
        '''either create a new state, or clone an earlier one '''
        self.csp_parent = csp_parent
        self.property_list = csp_parent.PropertyList
        if ncontainers:
            self.ncontainers = ncontainers
            self.containers = [CSP_Container(self.csp_parent) for i in range(ncontainers)]
        elif copy_state:
            self.ncontainers = copy_state.size()
            self.containers = [copy_state.get(i).clone() for i in range(self.ncontainers)]
        else:
            self.ncontainers = 0
            self.containers = []
    
    def get(self,index):
        return self.containers[index]
    
    def size(self):
        return self.ncontainers
    
    def print(self,msg=''):
        print (msg)
        for ic in range(self.ncontainers):
            self.containers[ic].print('c[%d]' % ic)
            
class CSP:
    
    def __init__(self,ncontainers):
        self.ncontainers = ncontainers
        self.PropertiesValues = {}
        self.PropertyList = []
        self.VCList = []
        self.INFList = []
        self.ConstraintPositions = []
        self.ConstraintNeighbors = []
        self.ConstraintPairs = []
        
    def setProperties(self,PropertiesValues):
        self.PropertiesValues = PropertiesValues
        self.PropertyList = list(self.PropertiesValues)
        
    def setConstraintPositions(self,constraints):
        self.ConstraintPositions = constraints
        
    def setConstraintPairs(self,constraints):
        self.ConstraintPairs = constraints
        
    def setConstraintNeighbors(self,constraints):
        self.ConstraintNeighbors = constraints
    
    def setViolationChecks(self,vc_list):
        self.VCList = vc_list
        
    def setInferences(self,inf_list):
        self.INFList = inf_list
        
    def solver(self):
        global ntrials,maxdone
        '''return {True|False},state'''
        self.stack = MyStack()
        # create a new state
        self.state = CSP_State(self,ncontainers=self.ncontainers)
        self.current_pos = [0,0,-1]  # [icontainer, iproperty, ivalue]
        
        while True:
            
            # try more values for the current property, checking violations, doing inferences, and checking violations again
            while not self.try_next_values():
                # nope, try to backtrack...
                if self.stack.isempty():
                    # nowhere to backtrack -- Failed completely
                    return False,None
                
                # no possible values for current property, so backtrack
                
                self.current_pos,self.state = self.stack.pop()
                #self.state.print('popped in solver',str(self.current_pos))
                
            
            # all right, we have a property/value that doesn't violate any rule
            # all inferences were performed, and no violations resulted

            mdone = self.count_values_used()
            if mdone > maxdone:
                maxdone = mdone
                #self.state.print('maxdone: %d, ntrials: %d' % (maxdone,ntrials))
            if ntrials % 100 == 0:
                #self.state.print('maxdone: %d, ntrials: %d' % (maxdone,ntrials))
                print (maxdone,ntrials)
                
            # check that all containers' properties have values, if so, we're done
            if self.success():
                return True,self.state
            
            # push current state and trials onto the stack
            #print('pushing: ',self.current_pos)
            #self.stack.push([self.current_pos, CSP_State(self,copy_state=self.state)])
            
            # find the next unset property
            self.find_next_unset_property()
            #print('next unset prop',self.current_pos)
                
            
    def success(self):
        '''return True if all containers properties have values'''
        for container in self.state.containers:
            for prop in self.PropertyList:
                if not container.getprop(prop):
                    return False
        return True
    
    def do_all_inferences(self):
        inferring = True
        while inferring:
            one_found = False
            for inf_func in self.INFList:
                if inf_func(self.state):
                    one_found = True
                    break
            if one_found:
                # do all inference functions again
                continue
            else:
                # no inferences succeeded, go to the next possibility
                inferring = False
        
    def check_all_violations(self):
        for viol in self.VCList:
            if not viol(self.state):
                return False
        return True
    
    def try_next_values(self):
        global ntrials,maxdone
        '''for the current container and current property, try next values until exhausted, or until
        a valid value is found for this container/property '''
        icontainer, iproperty, ivalue = self.current_pos
        #print('icontainer:',icontainer)
        #container.print()
        prop = self.PropertyList[iproperty]
        val_list = self.PropertiesValues[prop]
        
        valid_value = False
        for i in range(ivalue+1,len(val_list)):
            ntrials += 1
            # try the next value
            self.state.containers[icontainer].setprop(prop,val_list[i])
            # is it valid?
            if not self.check_all_violations():
                #print('tried: %d %s = %s (no)' % (icontainer,prop,val_list[i]))
                continue
            #print('tried: %d %s = %s (yes)' % (icontainer,prop,val_list[i]))
            # push the current state before changing any values via inferences
            self.stack.push([[icontainer,iproperty,i], CSP_State(self,copy_state=self.state)])
            #self.state.print('pushed in try_next:'+str([icontainer,iproperty,i]))
            # now do all inferences
            #print ('into all_inferences')
            self.do_all_inferences()
            #print ('out of all_inferences')
            # check again
            if not self.check_all_violations():
                # didn't make it, backtrack
                self.current_pos,self.state = self.stack.pop()
                #self.state.print('popped in try_next:'+str(self.current_pos))
            else:
                # all right - this is a good one
                self.current_pos = [icontainer,iproperty,i]
                #print('good next_value:',self.current_pos)
                return True
        #print('failed next_value:',self.current_pos)
        return False
    
    def find_next_unset_property(self):
        icontainer, iproperty, ivalue = self.current_pos
        nprops = len(self.PropertyList)
        for ic in range(icontainer,self.ncontainers):
            if ic == icontainer:
                start = iproperty+1
            else:
                start = 0
            for ip in range(0,nprops):
                if not self.state.containers[ic].getprop(self.PropertyList[ip]):
                    self.current_pos = [ic,ip,-1]
                    return
        self.state.print('Error: No unset properties (we should not be here)')
    
    def count_values_used(self):
        nused = 0
        for container in self.state.containers:
            for prop in self.PropertyList:
                if container.getprop(prop):
                    nused += 1
        return nused

In [5]:
ntrials = 0
maxdone = 0

Csp = CSP(3)

Csp.setProperties({'nationality':['Swede','Irish','Spanish'],\
                  'drink':['milk','beer','espresso'],\
                  'color':['green','magenta','red']})

Csp.setConstraintPositions([[0,'color','magenta']])

Csp.setConstraintPairs( [['nationality','Swede','drink','milk'],\
                        ['drink','beer','color','green'],\
                        ['nationality','Spanish','drink','espresso']])

Csp.setConstraintNeighbors( [['color','red','color','magenta',False],\
                            ['drink','milk','nationality','Irish',True]])

Csp.setViolationChecks([vc_all_different,vc_property_pair_in_same_container,vc_absolute_position,vc_neighbors])

Csp.setInferences([inf_all_different,inf_property_value_pairs,inf_absolute_position,inf_neighbors])

result,state = Csp.solver()

if result:
    print ('ntrials: %d, maxdone: %d' % (ntrials,maxdone))
    state.print('Answer!')
else:
    print('Failed')


ntrials: 4, maxdone: 9
Answer!
c[0] -- nationality: Spanish, drink: espresso, color: magenta
c[1] -- nationality: Swede, drink: milk, color: red
c[2] -- nationality: Irish, drink: beer, color: green
